In [ ]:
!pip install duckdb --no-index --find-links=/kaggle/input/polars-and-duckdb/kaggle/working/mysitepackages/duck_pkg
!pip install python-gdcm
!pip install pylibjpeg
!pip install pylibjpeg-libjpeg==2.2.0
!pip install pylibjpeg-openjpeg==2.3.0
!pip install matplotlib==3.10.3
!pip install scikit-learn==1.7.0
!pip install polars --no-index --find-links=/kaggle/input/polars-and-duckdb/kaggle/working/mysitepackages/polars_pkg
!pip install pydicom

In [ ]:
!pip install tensorflow-io==0.32.0
!pip install tensorflow==2.12.0

In [ ]:
!pip install tensorflow-io==0.37.1
!pip install tensorflow==2.16.1

In [1]:
from pydicom import dcmread
from pydicom.dataset import FileDataset, FileMetaDataset
from pydicom.uid import generate_uid, ImplicitVRLittleEndian

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import glob
import os
import polars as pl
import duckdb as dd
from tqdm import tqdm
import matplotlib.pyplot as plt
import cv2
import pickle
import gc
import ctypes
from pathlib import Path
import logging
import json
import multiprocessing as mp
from concurrent.futures import ProcessPoolExecutor
import datetime
import warnings
warnings.filterwarnings('ignore')

from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from sklearn.metrics import log_loss
import tensorflow as tf
import tensorflow_io as tfio
from tensorflow import keras

In [2]:
print(tf.__version__)
print(tfio.__version__)

2.16.1
0.37.1


In [ ]:
import sys
print(sys.version)

In [ ]:
for key, value in os.environ.items():
    print(f"{key}: {value}")

In [ ]:
tf.config.list_logical_devices('TPU')

In [3]:
strategy = tf.distribute.MirroredStrategy()

In [ ]:
print("All devices: ", tf.config.list_logical_devices('TPU'))

In [4]:
pl.Config(fmt_str_lengths=1000)
pl.Config.set_tbl_rows(1000)

polars.config.Config

In [5]:
allowed_tags = ['BitsAllocated', 'BitsStored', 'Rows', 'Columns', 'FrameOfReferenceUID', 'HighBit', 'ImageOrientationPatient'
                , 'ImagePositionPatient', 'InstanceNumber', 'Modality', 'PhotometricInterpretation'
                , 'PixelRepresentation', 'PixelSpacing', 'PlanarConfiguration', 'RescaleIntercept', 'RescaleSlope'
                , 'RescaleType', 'SamplesPerPixel', 'SliceThickness', 'SpacingBetweenSlices']

In [6]:
df_all_data = pl.read_parquet('/kaggle/input/rsna-aneurysm-train-metadata-suman/full_training_data.parquet')
print("Shape of training metadata", df_all_data.shape)
df_all_data.columns

Shape of training metadata (1001346, 24)


['file_name',
 'image_shape',
 'coordinates_x',
 'coordinates_y',
 'coordinates_f',
 'aneurysm_present_in_series',
 'aneurysm_present_in_image',
 'seriesinstanceuid',
 'patientage',
 'patientsex',
 'modality',
 'left_infraclinoid_internal_carotid_artery',
 'right_infraclinoid_internal_carotid_artery',
 'left_supraclinoid_internal_carotid_artery',
 'right_supraclinoid_internal_carotid_artery',
 'left_middle_cerebral_artery',
 'right_middle_cerebral_artery',
 'anterior_communicating_artery',
 'left_anterior_cerebral_artery',
 'right_anterior_cerebral_artery',
 'left_posterior_communicating_artery',
 'right_posterior_communicating_artery',
 'basilar_tip',
 'other_posterior_circulation']

In [7]:
#with tf.device('/device:TPU:0'):
root_folder = "/kaggle/input/rsna-intracranial-aneurysm-detection/series"

def create_full_image_path(row_data):
    return row_data['root_folder'] + '/' + row_data['seriesinstanceuid'] + '/' + row_data['file_name']

df_all_data = df_all_data.with_columns(pl.lit(root_folder).alias("root_folder"))

df_all_data = df_all_data.with_columns([
    pl.struct(pl.col("root_folder"), pl.col("seriesinstanceuid"), pl.col("file_name"))
    .map_elements(create_full_image_path, return_dtype=pl.String)
    .alias("full_image_path")
])

In [8]:
def extract_single_frame(multiframe_path, slice_number, output_path=None):
    """
    Extract a single frame from a multi-frame DICOM
    
    Args:
        multiframe_path: Path to multi-frame DICOM file
        slice_number: The slice number to extract (0-based index)
        output_path: Path to save the single-frame DICOM. If None, returns the dataset
    """
    try:
        # Read the multi-frame DICOM with force=True to handle potentially corrupted files
        multi_ds = dcmread(multiframe_path, force=True)
        
        # Verify it's a multi-frame image
        if not hasattr(multi_ds, 'NumberOfFrames'):
            raise ValueError("Input DICOM is not a multi-frame image")
        
        # Check if slice number is valid
        if slice_number >= multi_ds.NumberOfFrames:
            raise ValueError(f"Slice number {slice_number} is out of range. "
                           f"Image has {multi_ds.NumberOfFrames} frames")
        
        # Create new dataset for single frame
        single_ds = FileDataset(output_path or "temp.dcm", {}, 
                              file_meta=FileMetaDataset(), 
                              preamble=b"\0" * 128)
        
        # Copy attributes from multi-frame dataset
        attrs_to_copy = allowed_tags
        
        for attr in attrs_to_copy:
            if hasattr(multi_ds, attr):
                setattr(single_ds, attr, getattr(multi_ds, attr))
        
        # Generate new UIDs
        single_ds.SOPInstanceUID = generate_uid()
        single_ds.file_meta.MediaStorageSOPInstanceUID = single_ds.SOPInstanceUID
        
        # Set transfer syntax to uncompressed little endian
        single_ds.file_meta.TransferSyntaxUID = ImplicitVRLittleEndian
        single_ds.file_meta.MediaStorageSOPClassUID = multi_ds.file_meta.MediaStorageSOPClassUID
        if hasattr(multi_ds.file_meta, 'ImplementationClassUID'):
            single_ds.file_meta.ImplementationClassUID = multi_ds.file_meta.ImplementationClassUID
        
        # Set instance-specific attributes
        single_ds.InstanceNumber = slice_number + 1
        
        try:
            # Try to get pixel array directly
            pixel_array = multi_ds.pixel_array[slice_number]
        except Exception as e:
            #print(f"Warning: Could not directly access pixel_array: {e}")
            # Alternative approach: decompress and get pixels
            if hasattr(multi_ds, 'decompress'):
                multi_ds.decompress()
            pixel_array = multi_ds.pixel_array[slice_number]
        
        # Set pixel data
        single_ds.PixelData = pixel_array.tobytes()
        
        # Update image-specific attributes
        single_ds.NumberOfFrames = 1
        
        # Try to copy position and orientation
        try:
            if hasattr(multi_ds, 'PerFrameFunctionalGroupsSequence'):
                frame_content = multi_ds.PerFrameFunctionalGroupsSequence[slice_number]
                
                if hasattr(frame_content, 'PlanePositionSequence'):
                    position = frame_content.PlanePositionSequence[0].ImagePositionPatient
                    single_ds.ImagePositionPatient = position
                
                if hasattr(frame_content, 'PlaneOrientationSequence'):
                    orientation = frame_content.PlaneOrientationSequence[0].ImageOrientationPatient
                    single_ds.ImageOrientationPatient = orientation
        except Exception as e:
            #print(f"Warning: Could not copy position/orientation: {e}")
            raise
        
        # Add creation timestamp
        dt = datetime.datetime.now()
        single_ds.ContentDate = dt.strftime('%Y%m%d')
        single_ds.ContentTime = dt.strftime('%H%M%S.%f')
        
        # Save or return the dataset
        if output_path:
            single_ds.save_as(output_path, write_like_original=False)
            return None
        return single_ds
    
    except Exception as e:
        #print(f"Error extracting frame: {e}")
        raise

# Alternative version using different approach for compressed files
def extract_single_frame_alternative(multiframe_path, slice_number, output_path=None):
    """
    Alternative version for handling problematic files
    """
    try:
        # Read with force and stop before pixels
        multi_ds = dcmread(multiframe_path, force=True, stop_before_pixels=True)
        
        # Read pixel data separately
        with open(multiframe_path, 'rb') as f:
            multi_ds.PixelData = f.read()
        
        # Decompress if needed
        if hasattr(multi_ds, 'decompress'):
            multi_ds.decompress()
        
        # Get pixel array
        pixel_array = multi_ds.pixel_array[slice_number]
        
        # Create new dataset
        single_ds = FileDataset(output_path or "temp.dcm", {}, 
                              file_meta=FileMetaDataset(), 
                              preamble=b"\0" * 128)
        
        # Copy attributes (same as before)
        attrs_to_copy = allowed_tags
        
        for attr in attrs_to_copy:
            if hasattr(multi_ds, attr):
                setattr(single_ds, attr, getattr(multi_ds, attr))
        
        # Generate new UIDs
        single_ds.SOPInstanceUID = generate_uid()
        single_ds.file_meta.MediaStorageSOPInstanceUID = single_ds.SOPInstanceUID
        
        # Set transfer syntax to uncompressed little endian
        single_ds.file_meta.TransferSyntaxUID = ImplicitVRLittleEndian
        single_ds.file_meta.MediaStorageSOPClassUID = multi_ds.file_meta.MediaStorageSOPClassUID
        if hasattr(multi_ds.file_meta, 'ImplementationClassUID'):
            single_ds.file_meta.ImplementationClassUID = multi_ds.file_meta.ImplementationClassUID
        
        # Set instance-specific attributes
        single_ds.InstanceNumber = slice_number + 1
        
        try:
            # Try to get pixel array directly
            pixel_array = multi_ds.pixel_array[slice_number]
        except Exception as e:
            #print(f"Warning: Could not directly access pixel_array: {e}")
            # Alternative approach: decompress and get pixels
            if hasattr(multi_ds, 'decompress'):
                multi_ds.decompress()
            pixel_array = multi_ds.pixel_array[slice_number]
        
        # Set pixel data
        single_ds.PixelData = pixel_array.tobytes()
        
        # Update image-specific attributes
        single_ds.NumberOfFrames = 1
        
        # Try to copy position and orientation
        try:
            if hasattr(multi_ds, 'PerFrameFunctionalGroupsSequence'):
                frame_content = multi_ds.PerFrameFunctionalGroupsSequence[slice_number]
                
                if hasattr(frame_content, 'PlanePositionSequence'):
                    position = frame_content.PlanePositionSequence[0].ImagePositionPatient
                    single_ds.ImagePositionPatient = position
                
                if hasattr(frame_content, 'PlaneOrientationSequence'):
                    orientation = frame_content.PlaneOrientationSequence[0].ImageOrientationPatient
                    single_ds.ImageOrientationPatient = orientation
        except Exception as e:
            #print(f"Warning: Could not copy position/orientation: {e}")
            raise
        
        # Add creation timestamp
        dt = datetime.datetime.now()
        single_ds.ContentDate = dt.strftime('%Y%m%d')
        single_ds.ContentTime = dt.strftime('%H%M%S.%f')
        
        # Save or return the dataset
        if output_path:
            single_ds.save_as(output_path, write_like_original=False)
            return None
        return single_ds
        
    except Exception as e:
        #print(f"Error in alternative extraction: {e}")
        raise

# Function to try both methods
def safe_extract_single_frame(multiframe_path, slice_number, output_path=None):
    """
    Try both extraction methods
    """
    try:
        return extract_single_frame(multiframe_path, slice_number, output_path)
    except Exception as e:
        #print(f"Primary method failed: {e}")
        #print("Trying alternative method...")
        try:
            return extract_single_frame_alternative(multiframe_path, slice_number, output_path)
        except Exception as e2:
            #print(f"Alternative method also failed: {e2}")
            raise

# Version with zoom functionality
def load_and_view_single_slice_with_zoom(dcm_path, x_coord, y_coord, f_coord=None, zoom_size=100):
    """
    Load and display a single DICOM slice with crosshair and zoomed inset
    
    Args:
        dcm_path: Path to the DICOM file
        x_coord: x coordinate for the crosshair
        y_coord: y coordinate for the crosshair
        zoom_size: Size of the zoom window in pixels
    """
    # Read DICOM file
    if f_coord:
        ds = safe_extract_single_frame(dcm_path, f_coord)
    else:
        ds = dcmread(dcm_path)
    img = ds.pixel_array
    
    # Create figure and axes
    fig, (ax1, ax2) = plt.subplots(1, 2, figsize=(15, 7))
    
    # Main image with crosshair
    ax1.imshow(img, cmap='gray')
    ax1.axvline(x=x_coord, color='red', alpha=0.5)
    ax1.axhline(y=y_coord, color='red', alpha=0.5)
    ax1.plot(x_coord, y_coord, 'r+', markersize=10, markeredgewidth=2)
    
    # Zoomed region
    x_start = int(max(0, x_coord - zoom_size/2))
    x_end = int(min(img.shape[1], x_coord + zoom_size/2))
    y_start = int(max(0, y_coord - zoom_size/2))
    y_end = int(min(img.shape[0], y_coord + zoom_size/2))
    
    zoomed = img[y_start:y_end, x_start:x_end]
    ax2.imshow(zoomed, cmap='gray')
    
    # Add crosshair to zoomed region
    center_x = x_coord - x_start
    center_y = y_coord - y_start
    ax2.axvline(x=center_x, color='red', alpha=0.5)
    ax2.axhline(y=center_y, color='red', alpha=0.5)
    ax2.plot(center_x, center_y, 'r+', markersize=10, markeredgewidth=2)
    
    ax1.axis('off')
    ax2.axis('off')
    ax1.set_title('Full Image')
    ax2.set_title('Zoomed Region')
    
    plt.tight_layout()
    plt.show()

In [117]:
def read_and_parse_dicom_files_tensorflow_train(dcm_path, f_coord=None):
    raw_image = tf.io.read_file(dcm_path)
    image = tfio.image.decode_dicom_image(raw_image, scale='auto', dtype=tf.float32)
    #if f_coord:
    specific_slice_tensor = tf.slice(
        image,
        begin=[f_coord, 0, 0, 0],
        size=[1, image.shape[1], image.shape[2], image.shape[3]]
    )
    # Squeeze to remove the extra dimension of size 1
    specific_slice_tensor = tf.squeeze(specific_slice_tensor)
    """else:
        specific_slice_tensor = tf.squeeze(image)"""
    expanded_image = tf.expand_dims(specific_slice_tensor, -1)
    m, M=tf.math.reduce_min(expanded_image), tf.math.reduce_max(expanded_image)
    expanded_image = (tf.image.grayscale_to_rgb(expanded_image)-m)/(M-m)
    expanded_image = tf.image.resize(expanded_image, (128,128))
    sqzd_image = tf.squeeze(expanded_image)
    return sqzd_image

def load_dicom_tf(filepath_tensor, f_coord_tensor=None):
    """
    Wrapper function to call read_and_parse_dicom_files_tensorflow_train within a tf.data.Dataset pipeline.
    """
    #if f_coord_tensor:
    image = tf.py_function(
        read_and_parse_dicom_files_tensorflow_train,
        inp=[filepath_tensor, f_coord_tensor],
        Tout=tf.float32 # Adjust Tout based on the expected output type of your image data
    )
    """else:
        image = tf.py_function(
            read_and_parse_dicom_files_tensorflow_train,
            inp=[filepath_tensor],
            Tout=tf.float32 # Adjust Tout based on the expected output type of your image data
    )"""
    # Ensure the shape is defined if known, as tf.py_function can lose shape info
    #image.set_shape([128, 128]) # Example for a 2D image, adjust as needed
    return image 

def preprocessing(dcm_path, f_coord):
    train_img = load_dicom_tf(dcm_path, f_coord)
    #train_img = read_and_parse_dicom_files_tensorflow_train(dcm_path, f_coord)
    train_img = tf.reshape(train_img, shape=(128, 128, 3))
    return train_img

def load_dataset_tensorflow_train(dcm_path, f_coord, labels):
    image = preprocessing(dcm_path, f_coord)
    return {"images": tf.cast(image, tf.float32), "labels": tf.cast(labels, tf.float32)}

def dict_to_tuple(inputs):
    return inputs["images"], inputs["labels"]

In [10]:
cols_to_select = ['full_image_path', 'coordinates_f', 'left_infraclinoid_internal_carotid_artery',  'right_infraclinoid_internal_carotid_artery',  'left_supraclinoid_internal_carotid_artery'
                  ,  'right_supraclinoid_internal_carotid_artery',  'left_middle_cerebral_artery',  'right_middle_cerebral_artery',  'anterior_communicating_artery'
                  ,  'left_anterior_cerebral_artery',  'right_anterior_cerebral_artery',  'left_posterior_communicating_artery',  'right_posterior_communicating_artery'
                  ,  'basilar_tip',  'other_posterior_circulation'
]

df_for_train_baseline = df_all_data.select(cols_to_select)

In [11]:
x_train, x_test_val = train_test_split(df_for_train_baseline, test_size=0.4, random_state=42)
x_test, x_valid = train_test_split(x_test_val, test_size=0.2, random_state=42)

print("Training data shape : {0}".format(x_train.shape))
print("Test data shape : {0}".format(x_test.shape))
print("Validation data shape : {0}".format(x_valid.shape))

Training data shape : (600807, 15)
Test data shape : (320431, 15)
Validation data shape : (80108, 15)


In [ ]:
test_with_slice = dd.sql("select * from x_train where coordinates_f != 0 limit 10").pl()

In [14]:
label_cols = ['left_infraclinoid_internal_carotid_artery',  'right_infraclinoid_internal_carotid_artery',  'left_supraclinoid_internal_carotid_artery'
                  ,  'right_supraclinoid_internal_carotid_artery',  'left_middle_cerebral_artery',  'right_middle_cerebral_artery',  'anterior_communicating_artery'
                  ,  'left_anterior_cerebral_artery',  'right_anterior_cerebral_artery',  'left_posterior_communicating_artery',  'right_posterior_communicating_artery'
                  ,  'basilar_tip',  'other_posterior_circulation'
]

In [ ]:
dd.sql("select left_infraclinoid_internal_carotid_artery, count(distinct(full_image_path)) \
from x_train group by left_infraclinoid_internal_carotid_artery").pl()

In [ ]:
with tf.device('/device:TPU:1'):
    x_train_agg = x_train.group_by('left_infraclinoid_internal_carotid_artery').agg(pl.col("full_image_path").count())
    list_of_classes = pl.Series(x_train_agg.select('left_infraclinoid_internal_carotid_artery')).to_list()
    bias_arr_prep_dict = {}
    for cls in list_of_classes:
        print(cls)
        print(x_train_agg.filter(pl.col('left_infraclinoid_internal_carotid_artery')==cls)\
              .select(pl.col('full_image_path')).item(0, 0))
        bias_arr_prep_dict[cls] = x_train_agg.filter(pl.col('left_infraclinoid_internal_carotid_artery')==cls)\
        .select(pl.col('full_image_path')).item(0, 0)
        
    print(bias_arr_prep_dict)

In [ ]:
strategy.num_replicas_in_sync

In [115]:
def generate_tf_datasets(p_df, p_BATCH_SIZE_PER_REPLICA):

    #BATCH_SIZE = p_BATCH_SIZE_PER_REPLICA * tpu_strategy.num_replicas_in_sync
    BATCH_SIZE = p_BATCH_SIZE_PER_REPLICA
    
    image_filenames = pl.Series(p_df.select(pl.col('full_image_path'))).to_list()
    #print("image_filenames - ", image_filenames)
    image_f_coords = pl.Series(p_df.select(pl.col('coordinates_f'))).fill_null(0).to_list()
    #print("image_f_coords - ", image_f_coords)
    #image_labels = pl.Series(p_df.select(label_cols)).to_list()
    image_labels = pl.Series(p_df.select(label_cols)).map_elements(lambda d: list(d.values())).to_list()
    #print("image_labels - ", image_labels)
    
    image_dataset = tf.data.Dataset.from_tensor_slices((image_filenames, image_f_coords, image_labels))
    #print("type image_dataset - ", type(image_dataset))
    
    image_ds = image_dataset.map(load_dataset_tensorflow_train, num_parallel_calls=tf.data.AUTOTUNE)
    #print("type image_ds - ", type(image_ds))
    image_ds = image_ds.map(dict_to_tuple, num_parallel_calls=tf.data.AUTOTUNE)
    image_ds = image_ds.batch(batch_size=BATCH_SIZE, drop_remainder=True)
    image_ds = image_ds.prefetch(tf.data.AUTOTUNE)
    
    return image_ds

In [99]:
x_train.head(375)

shape: (375, 15)
┌───────────┬───────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ full_imag ┆ coordinat ┆ left_infr ┆ right_inf ┆ … ┆ left_post ┆ right_pos ┆ basilar_t ┆ other_po │
│ e_path    ┆ es_f      ┆ aclinoid_ ┆ raclinoid ┆   ┆ erior_com ┆ terior_co ┆ ip        ┆ sterior_ │
│ ---       ┆ ---       ┆ internal_ ┆ _internal ┆   ┆ municatin ┆ mmunicati ┆ ---       ┆ circulat │
│ str       ┆ i32       ┆ carotid_a ┆ _carotid_ ┆   ┆ g_artery  ┆ ng_artery ┆ i64       ┆ ion      │
│           ┆           ┆ rtery     ┆ artery    ┆   ┆ ---       ┆ ---       ┆           ┆ ---      │
│           ┆           ┆ ---       ┆ ---       ┆   ┆ i64       ┆ i64       ┆           ┆ i64      │
│           ┆           ┆ i64       ┆ i64       ┆   ┆           ┆           ┆           ┆          │
╞═══════════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ /kaggle/i ┆ null      ┆ 0         ┆ 0         ┆ … ┆ 0         ┆ 0         ┆ 0         ┆ 0        │
│ nput/rsna ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ -intracra ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ nial-aneu ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ rysm-dete ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ ction/ser ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ ies/1.2.8 ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 26.0.1.36 ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 80043.8.4 ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 98.886873 ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 514159263 ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 054188962 ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 281113088 ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 09946/1.2 ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ .826.0.1. ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 3680043.8 ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ .498.7587 ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 534120824 ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 043995349 ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 131569888 ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 7962133.d ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ cm        ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ /kaggle/i ┆ null      ┆ 0         ┆ 0         ┆ … ┆ 0         ┆ 0         ┆ 0         ┆ 0        │
│ nput/rsna ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ -intracra ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ nial-aneu ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ rysm-dete ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ ction/ser ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ ies/1.2.8 ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 26.0.1.36 ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ 80043.8.4 ┆           ┆           ┆       

In [119]:
x_trial = x_train.slice(offset=0, length=100000)
x_trial.shape

(100000, 15)

In [120]:
train_ds = generate_tf_datasets(p_df=x_trial, p_BATCH_SIZE_PER_REPLICA = 10)

In [29]:
test_ds = generate_tf_datasets(p_df=x_test.slice(offset=1, length=100), p_BATCH_SIZE_PER_REPLICA = 10)
valid_ds = generate_tf_datasets(p_df=x_valid.slice(offset=1, length=100), p_BATCH_SIZE_PER_REPLICA = 10)

In [17]:
train_ds = generate_tf_datasets(p_df=x_train, p_BATCH_SIZE_PER_REPLICA = 10)

ValueError: Attempt to convert a value (None) with an unsupported type (<class 'NoneType'>) to a Tensor.

In [28]:
for images, labels in train_ds.take(5):
    print(f"Features: {images.numpy().shape}, Labels: {labels.numpy().shape}")

W: processing MR image ... applying modality transform may create unexpected result
W: processing MR image ... applying modality transform may create unexpected result
W: processing MR image ... applying modality transform may create unexpected result


Features: (10, 128, 128, 3), Labels: (10, 13)
Features: (10, 128, 128, 3), Labels: (10, 13)
Features: (10, 128, 128, 3), Labels: (10, 13)
Features: (10, 128, 128, 3), Labels: (10, 13)
Features: (10, 128, 128, 3), Labels: (10, 13)


W: processing MR image ... applying modality transform may create unexpected result
W: invalid value for 'OverlayBitPosition' (12), refers to bit position within stored pixel value


In [39]:
from tensorflow.keras.applications import EfficientNetB0
from tensorflow.keras import layers

with strategy.scope():
    
    rsna_input = layers.Input(shape=(128,128,3), name="rsna_input")

    conv_base = EfficientNetB0(include_top=False, weights="imagenet", input_tensor=rsna_input)
    conv_base.trainable = False

    max_pool_layer_0 = layers.MaxPooling2D(name="max_pool_0", pool_size=(2, 2), strides=(1, 1), padding="same")(conv_base.output)
    max_pool_layer_0 = layers.BatchNormalization()(max_pool_layer_0)

    conv2d_1 = layers.Conv2D(filters=100, kernel_size=4, strides=1, padding="same", activation="relu")(max_pool_layer_0)
    max_pool_layer_1 = layers.MaxPooling2D(name="max_pool_1", pool_size=(2, 2), strides=(1, 1), padding="same")(conv2d_1)
    max_pool_layer_1 = layers.BatchNormalization()(max_pool_layer_1)

    flattened_layer = layers.Flatten()(max_pool_layer_1)

    hidden_layer1 = layers.Dense(200, activation="selu", kernel_initializer=keras.initializers.LecunNormal(seed=None))(flattened_layer)
    hidden_layer1 = layers.BatchNormalization()(hidden_layer1)
    hidden_layer2 = layers.Dense(100, activation="selu", kernel_initializer=keras.initializers.LecunNormal(seed=None))(hidden_layer1)
    hidden_layer2 = layers.BatchNormalization()(hidden_layer2)
    hidden_layer3 = layers.Dense(50, activation="selu", kernel_initializer=keras.initializers.LecunNormal(seed=None))(hidden_layer2)
    hidden_layer3 = layers.BatchNormalization()(hidden_layer3)
    rsna_output = layers.Dense(13, activation="sigmoid")(hidden_layer3)
    model1 = tf.keras.Model(rsna_input, rsna_output)

    checkpoint_cb = tf.keras.callbacks.ModelCheckpoint("keras_effnet_test.keras")
    early_stopping_cb = tf.keras.callbacks.EarlyStopping(patience=5, restore_best_weights=True)

    model1.compile(loss="binary_crossentropy", optimizer="adamax", metrics=["accuracy"])

In [40]:
with strategy.scope():
    history = model1.fit(train_ds, epochs=22, validation_data=valid_ds, callbacks=[checkpoint_cb, early_stopping_cb])

W: processing MR image ... applying modality transform may create unexpected result
W: processing MR image ... applying modality transform may create unexpected result
W: processing MR image ... applying modality transform may create unexpected result
W: processing MR image ... applying modality transform may create unexpected result
W: invalid value for 'OverlayBitPosition' (12), refers to bit position within stored pixel value


Epoch 1/22


W: processing MR image ... applying modality transform may create unexpected result
W: processing MR image ... applying modality transform may create unexpected result
W: processing MR image ... applying modality transform may create unexpected result


 1/10 ━━━━━━━━━━━━━━━━━━━━ 1:12 8s/step - accuracy: 0.0000e+00 - loss: 0.8535

W: processing MR image ... applying modality transform may create unexpected result
W: invalid value for 'OverlayBitPosition' (12), refers to bit position within stored pixel value


...

 1/10 ━━━━━━━━━━━━━━━━━━━━ 4s 515ms/step - accuracy: 0.0000e+00 - loss: 0.3190

W: processing MR image ... applying modality transform may create unexpected result
W: invalid value for 'OverlayBitPosition' (12), refers to bit position within stored pixel value


10/10 ━━━━━━━━━━━━━━━━━━━━ 0s 161ms/step - accuracy: 0.0000e+00 - loss: 0.3141

W: processing MR image ... applying modality transform may create unexpected result
W: processing MR image ... applying modality transform may create unexpected result
W: processing MR image ... applying modality transform may create unexpected result
W: processing MR image ... applying modality transform may create unexpected result
W: processing MR image ... applying modality transform may create unexpected result
W: processing MR image ... applying modality transform may create unexpected result


10/10 ━━━━━━━━━━━━━━━━━━━━ 5s 461ms/step - accuracy: 0.0000e+00 - loss: 0.3137 - val_accuracy: 1.0000 - val_loss: 0.2940


In [42]:
def read_and_parse_dicom_files_tensorflow_infer(dcm_path, f_coord=None):
    tf.config.run_functions_eagerly(True)
    raw_image = tf.io.read_file(dcm_path)
    image = tfio.image.decode_dicom_image(raw_image, scale='auto', dtype=tf.float32)
    if f_coord:
        specific_slice_tensor = tf.slice(
            image,
            begin=[f_coord, 0, 0, 0],
            size=[1, image.shape[1], image.shape[2], image.shape[3]]
        )
        # Squeeze to remove the extra dimension of size 1
        specific_slice_tensor = tf.squeeze(specific_slice_tensor)
    else:
        specific_slice_tensor = tf.squeeze(image)
    #print("specific_slice_tensor - ", specific_slice_tensor.shape)
    expanded_image = tf.expand_dims(specific_slice_tensor, -1)
    m, M=tf.math.reduce_min(expanded_image), tf.math.reduce_max(expanded_image)
    expanded_image = (tf.image.grayscale_to_rgb(expanded_image)-m)/(M-m)
    expanded_image = tf.image.resize(expanded_image, (128,128))
    sqzd_image = tf.squeeze(expanded_image)
    #print("sqzd_image -", sqzd_image.shape)
    return sqzd_image

In [43]:
image_filenames = pl.Series(x_valid.select(pl.col('full_image_path'))).to_list()[0]
image_f_coords = pl.Series(x_valid.select(pl.col('coordinates_f'))).to_list()[0]
image_labels = pl.Series(x_valid.select(label_cols)).map_elements(lambda d: list(d.values())).to_list()[0]

In [44]:
test_image = \
read_and_parse_dicom_files_tensorflow_infer(image_filenames, image_f_coords)

In [45]:
test_image.shape

TensorShape([128, 128, 3])

In [46]:
test_image_for_inf = np.expand_dims(test_image, axis=0)
test_image_for_inf.shape

(1, 128, 128, 3)

In [47]:
prediction = model1.predict(test_image_for_inf)

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 415ms/step


In [48]:
prediction.shape

(1, 13)

In [49]:
prediction

array([[0.39659363, 0.2816998 , 0.1800119 , 0.2959862 , 0.15417872,
        0.29453218, 0.24033053, 0.23615861, 0.2773422 , 0.20688261,
        0.22964416, 0.22283424, 0.2877473 ]], dtype=float32)